<a href="https://colab.research.google.com/github/mariamiguelr/DSM/blob/main/tentativa2_albertina.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Variant Identifier

> Note: For the code tu run faster, change the runtime of this notebook to have a GPU.
On the top tab select "Runtime > Change runtime type > GPU". This change will make the code run in seconds rather than hours...

In an era where chat bots are becoming ubiquitous tools, a significant concern arises: how can we ensure these tools benefit all societies? One major hurdle in achieving this inclusivity is the scarcity of language variant-specific models. For example, while Portuguese is not considered a low-resource language, the majority of available content is in Brazilian Portuguese. Consequently, a language model trained in a Portuguese corpus (without any concern regarding its variants) is likely to exhibit a bias towards producing text in Brazilian Portuguese. What are the implications of such a bias? Countries like Portugal could find themselves at a disadvantage, particularly in deploying language model-based systems in critical areas such as healthcare and judiciary, where the distinct nuances of Portuguese are of great importance.

With this context in mind, your task in this assignment is to develop a model capable of classifying texts as either European Portuguese or Brazilian Portuguese. Below is the quick start code to guide you.

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

MessageError: Error: credential propagation was unsuccessful

In [ ]:
import pandas as pd


In [ ]:
 %pip install --quiet datasets

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 542.0/542.0 kB 8.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 9.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 11.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 10.8 MB/s eta 0:00:00


In [ ]:
%pip install torch

  Using cached nvidia_cuda_nvrtc_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (23.7 MB)
  Using cached nvidia_cuda_runtime_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (823 kB)
  Using cached nvidia_cuda_cupti_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (14.1 MB)
  Using cached nvidia_cudnn_cu12-8.9.2.26-py3-none-manylinux1_x86_64.whl (731.7 MB)
  Using cached nvidia_cublas_cu12-12.1.3.1-py3-none-manylinux1_x86_64.whl (410.6 MB)
  Using cached nvidia_cufft_cu12-11.0.2.54-py3-none-manylinux1_x86_64.whl (121.6 MB)
  Using cached nvidia_curand_cu12-10.3.2.106-py3-none-manylinux1_x86_64.whl (56.5 MB)
  Using cached nvidia_cusolver_cu12-11.4.5.107-py3-none-manylinux1_x86_64.whl (124.2 MB)
  Using cached nvidia_cusparse_cu12-12.1.0.106-py3-none-manylinux1_x86_64.whl (196.0 MB)
  Using cached nvidia_nccl_cu12-2.20.5-py3-none-manylinux2014_x86_64.whl (176.2 MB)
  Using cached nvidia_nvtx_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (99 kB)
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.3/21

In [ ]:
import torch

DEVICE = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Device {DEVICE} available.")

Device cuda available.


In [ ]:
from datasets import load_dataset

dataset = load_dataset("cc4051/pt_vid")
dataset

DatasetDict({
    train: Dataset({
        features: ['text', 'label'],
        num_rows: 11717
    })
    test: Dataset({
        features: ['text', 'label'],
        num_rows: 2570
    })
})

In [ ]:
print("Number of training examples: ", len(dataset["train"]))
print("Example: ", dataset["train"][0])

Number of training examples:  11717
Example:  {'text': 'Direita italiana inicia processo de coligação para as eleições de Março A alternativa «civilizada» Eduardo Tessler, em Roma O deputado reformador Mario Segni fez ontem um acordo com a Liga Norte para criar uma aliança eleitoral de centro-direita, para concorrer às legislativas italianas de Março. É a tentativa de constituir uma alternativa da «direita civilizada» à coligação das esquerdas, liderada pelo PDS. E ainda de «domesticar» a Liga. Mas falta saber a resposta do Partido Popular (ex-democracia Cristã) e a reacção do magnata Berlusconi.', 'label': 0}


In [ ]:
dataset["train"][0]['text']

'Direita italiana inicia processo de coligação para as eleições de Março A alternativa «civilizada» Eduardo Tessler, em Roma O deputado reformador Mario Segni fez ontem um acordo com a Liga Norte para criar uma aliança eleitoral de centro-direita, para concorrer às legislativas italianas de Março. É a tentativa de constituir uma alternativa da «direita civilizada» à coligação das esquerdas, liderada pelo PDS. E ainda de «domesticar» a Liga. Mas falta saber a resposta do Partido Popular (ex-democracia Cristã) e a reacção do magnata Berlusconi.'

Na versão do HuggingFace as labels tem o seguinte mapeamento:

In [ ]:
label_map = {
    0: "PT-PT",
    1: "PT-BR",
}

n_classes = len(label_map)

In [ ]:
#dataset["train"]['text']

'Direita italiana inicia processo de coligação para as eleições de Março A alternativa «civilizada» Eduardo Tessler, em Roma O deputado reformador Mario Segni fez ontem um acordo com a Liga Norte para criar uma aliança eleitoral de centro-direita, para concorrer às legislativas italianas de Março. É a tentativa de constituir uma alternativa da «direita civilizada» à coligação das esquerdas, liderada pelo PDS. E ainda de «domesticar» a Liga. Mas falta saber a resposta do Partido Popular (ex-democracia Cristã) e a reacção do magnata Berlusconi.Compton\'s New Media chega ao Brasil Empresa será representada pela norte-americana Devell e promete editar títulos criados por brasileiros MARIA EDICY MOREIRA Free-lance para a Folha A Compton\'s NewMedia, uma das maiores produtoras de CD-ROM dos EUA, chega ao Brasil esta semana. A empresa, detentora de 42% do mercado norte-americano de CD-ROM, será representada pela Devell USA. O anúncio foi feito na semana passada, em São Paulo, por Christopher 

## Data Cleanup

In [ ]:
"ABABABAB".lower() # to have all words in lower case (try with "ABABAB")

'abababab'

## Loading more datasets

In [ ]:
# More datasets
!git clone https://github.com/LanguageTechnologyLab/DSL-TL.git


Cloning into 'DSL-TL'...
remote: Enumerating objects: 569, done.
remote: Counting objects: 100% (223/223), done.
remote: Compressing objects: 100% (144/144), done.
remote: Total 569 (delta 87), reused 179 (delta 76), pack-reused 346
Receiving objects: 100% (569/569), 3.99 MiB | 8.75 MiB/s, done.
Resolving deltas: 100% (270/270), done.


In [ ]:
cd DSL-TL/DSL-TL-Corpus/PT-DSL-TL


/content/DSL-TL/DSL-TL-Corpus/PT-DSL-TL


In [ ]:
# Replace 'file_name.csv' with the actual file name

file_name = 'PT_train.tsv'
dataset2 = pd.read_csv(file_name, sep="\t")

print(dataset2.head())



   155907 Confira a matéria que foi ao ar nesta segunda-feira, 28, no "CQC:  \
0  155413  O projeto será apresentado pelo presidente em ...                  
1  173135  As nomeações terminam às 12 horas do próximo d...                  
2  156093  “Um programa imperdível para quem vai a Porto ...                  
3  173776  A quebra na venda de casas surge numa altura e...                  
4  174093  A Portugal Telecom (PT) perdeu o recurso contr...                  

   PT-BR  
0  PT-BR  
1  PT-BR  
2  PT-BR  
3  PT-PT  
4  PT-PT  


Let's train a simple model.

In [ ]:
import re

corpus = "".join(dataset["train"]["text"]) # one giant sentence

# we will define our vocab to be composed of
vocab = list(set(corpus.lower()))
# remove punctuation
vocab = list(set(re.sub(r'[^\w\s]', '', token) for token in vocab))
# remove numbers
vocab = list(set(re.sub('[0-9]', '', token) for token in vocab))
# remove non-ascii chars (optional)
vocab = list(set(re.sub(r'[^\x00-x7F]+', '', token) for token in vocab))

# Special padding token
pad_token = "<pad>"
vocab.append(pad_token)

# Special unknown token
unk_token = "<unk>"
vocab.append(unk_token)

n_tokens = len(vocab)

print("Number of tokens in the vocab: ", n_tokens)

Number of tokens in the vocab:  28


In [ ]:
tkn2id = {v: k for k, v in enumerate(vocab)}

pad_token_id = tkn2id[pad_token]
unk_token_id = tkn2id[unk_token]


def tokenize(text):
    return [tkn2id[c] if c in tkn2id else unk_token_id for c in text.lower()]


In [ ]:
example = "Olá, tudo bem?"

print("Example: ", example)
print("Tokenized: ", tokenize(example))

Example:  Olá, tudo bem?
Tokenized:  [11, 13, 27, 27, 10, 16, 17, 4, 11, 10, 14, 25, 22, 27]


For the first model we will use an LDA model

In [ ]:
import gensim
import warnings

with warnings.catch_warnings():
    warnings.simplefilter('ignore')
    lda_train = gensim.models.ldamulticore.LdaMulticore(
                           corpus=train_corpus,
                           num_topics=20,
                           id2word=train_id2word,
                           chunksize=100,
                           workers=7, # Num. Processing Cores - 1
                           passes=50,
                           eval_every = 1,
                           per_word_topics=True)
    lda_train.save('lda_train.model')

NameError: name 'train_corpus' is not defined

For the architecture, we will use an LSTM based model as it deals well with different size inputs (we can have a text with 20 characters or 2,000).

In [ ]:
import torch
import torch.nn as nn
import torch.nn.functional as F

#artificial recurrent neural network (RNN)

class Model(nn.Module):
    def __init__(
        self,
        vocab_size: int,
        hidden_size: int,
        n_classes: int,
        n_layers: int
    ):
        super(Model, self).__init__()
        self.embedding = nn.Embedding(
            vocab_size,
            int(hidden_size),
            padding_idx=pad_token_id
        )
        self.rnn = nn.LSTM(
            int(hidden_size),
            int(hidden_size),
            batch_first=True,
            num_layers=int(n_layers),
        )
        self.fc = nn.Linear(int(hidden_size), n_classes)

    def forward(self, x):
        x = self.embedding(x)
        x, _ = self.rnn(x)
        x = F.relu(x)
        x = x[:, -1, :]  # get the last hidden state
        logits = self.fc(x)
        return logits

Now we build a torch dataloader to facilitate training.

In [ ]:
from torch.utils.data import DataLoader, Dataset


class VIdDataset(Dataset):
    def __init__(self, data, tokenizer, max_length=512):
        """The max_length limits the number of tokens in the text.
        Texts that are longer are truncated, and shorter texts are padded."""
        self.data = data
        self.tokenizer = tokenizer
        self.max_length = max_length
        self.pad_token_id = pad_token_id

    def __len__(self):
        return len(self.data)

    def __getitem__(self, idx):
        item = self.data[idx]
        text = item["text"]
        tokens = self.tokenizer(text)
        if len(tokens) < self.max_length:  # padding
            padding = [self.pad_token_id] * (self.max_length - len(tokens))
            tokens += padding
        else:  # truncate
            tokens = tokens[: self.max_length]

        label = item["label"]
        return {
            "tokens": torch.tensor(tokens),
            "label": torch.tensor(label),
        }

In [ ]:
train_dataset = VIdDataset(dataset["train"], tokenize)
train_loader = DataLoader(
    dataset=train_dataset,
    batch_size=64,
    shuffle=True,
    drop_last=True
  )

In [ ]:
#train function

from torch import optim
from tqdm import tqdm

def train(
    model: nn.Module,
    train_loader: DataLoader,
    n_epochs: int,
    lr: float,
) -> tuple[float, float]:
  """
  Trains the model on the provided training data with early stopping.

  Args:
      model: The PyTorch model to train.
      train_loader: The DataLoader containing the training data.
      n_epochs: The number of epochs to train for.
      lr: The learning rate to use for training.

  Returns:
      A tuple containing the average training loss and accuracy over the entire training process.
  """

  optimizer = optim.AdamW(model.parameters(), lr=lr)
  criteria = nn.CrossEntropyLoss()

  for epoch in range(n_epochs):
    model.train()

    n_steps = len(train_loader)
    progress_bar = tqdm(
        total=n_steps, desc=f"Epoch {epoch+1}", position=0, leave=True
    )
    total_loss = 0
    total_correct = 0

    for idx, batch in enumerate(train_loader):
      optimizer.zero_grad()
      x = batch["tokens"].to(DEVICE)
      y = batch["label"].to(DEVICE)
      logits = model(x)
      loss = criteria(logits, y)
      loss.backward()
      optimizer.step()

      # Logging and early stopping check
      total_loss += loss.item()
      y_pred = logits.argmax(dim=1)
      total_correct += (y_pred == y).sum().item()

      progress_bar.set_postfix({
          "loss": total_loss / (idx + 1),
          "accuracy": total_correct / (idx + 1) / x.size(0)
      })
      progress_bar.update()


      avg_loss = total_loss / n_steps
      avg_accuracy = total_correct / (n_steps * x.size(0))

    return avg_loss, avg_accuracy



We now have the model and the data so we are ready to build our training loop.

In [ ]:
def objective_function(params):
  """
  Objective function for hyperparameter optimization with early stopping.

  Args:
      params: A dictionary containing the hyperparameter values.

  Returns:
      A tuple containing the average training loss (or a large negative value
      in case of errors).
  """

  model = Model(vocab_size=n_tokens,
                hidden_size=params['hidden_size'],
                n_classes=n_classes,
                n_layers=params['n_layers'])

  if torch.cuda.is_available():
    model.to(DEVICE)

  try:
    avg_loss, _ = train(model, train_loader, n_epochs=10, lr=params['lr'])


  except Exception as e:
    print(f"Error during training: {e}")
    # Return a large negative value to indicate poor performance
    return -100

  if math.isnan(avg_loss):
    avg_loss = -100
  print(f"avg_loss before return: {avg_loss}")
  return avg_loss

In [ ]:
from hyperopt import hp, fmin, tpe
import math

search_space = {
  'lr': hp.loguniform('lr', -6, -3),  # Learning rate search space
  'hidden_size': hp.quniform('hidden_size', 64, 256, 8),  # Hidden size search space
  'n_layers': hp.quniform('n_layers', 1, 3, 1)  # Number of layers search space
}

# Optimize the hyperparameters using Bayesian optimization
best_params = fmin(fn=objective_function,
                   space=search_space,
                   algo=tpe.suggest,  # TPE algorithm for Bayesian optimization
                   max_evals=50)  # Adjust max_evals based on computational resources

# Use the best_params to train the final model
model = Model(vocab_size=n_tokens,
                hidden_size=best_params['hidden_size'],
                n_classes=n_classes,
                n_layers=best_params['n_layers'])

  0%|          | 0/50 [00:00<?, ?trial/s, best loss=?]

Epoch 1:   4%|4         | 8/183 [00:01<00:30,  5.69it/s, loss=0.787, accuracy=0.613]


Early stopping triggered at epoch
1
  0%|          | 0/50 [00:01<?, ?trial/s, best loss=?]

Epoch 1:   4%|4         | 8/183 [00:01<00:35,  4.92it/s, loss=0.787, accuracy=0.613]


avg_loss before return: -100
  2%|▏         | 1/50 [00:01<01:20,  1.64s/trial, best loss: -100.0]

...

avg_loss before return: -100
 98%|█████████▊| 49/50 [01:06<00:01,  1.42s/trial, best loss: -100.0]

Epoch 1:   7%|6         | 12/183 [00:02<00:30,  5.65it/s, loss=0.626, accuracy=0.667]


Early stopping triggered at epoch
1
 98%|█████████▊| 49/50 [01:09<00:01,  1.42s/trial, best loss: -100.0]

Epoch 1:   7%|6         | 12/183 [00:02<00:32,  5.20it/s, loss=0.626, accuracy=0.667]


avg_loss before return: -100
100%|██████████| 50/50 [01:09<00:00,  1.38s/trial, best loss: -100.0]


In [ ]:
best_params

{'hidden_size': 160.0, 'lr': 0.003340031578480459, 'n_layers': 3.0}

In [ ]:
best_hidden_size = best_params['hidden_size']
best_n_layers = best_params['n_layers']
best_lr = best_params['lr']

model = Model(vocab_size=n_tokens,
              hidden_size=best_hidden_size,
              n_classes=n_classes,
              n_layers=best_n_layers)



TypeError: Model.__init__() got an unexpected keyword argument 'vocab_size'

In [ ]:
 n_epochs= 20
 for epoch in range(n_epochs):
    print(f"Epoch: {epoch+1}")  # Track current epoch
    train(model, train_loader, n_epochs=n_epochs, lr=best_lr)

Epoch: 1


Epoch 1: 100%|██████████| 183/183 [00:32<00:00,  5.58it/s, loss=0.596, accuracy=0.716]


Epoch: 2


Epoch 1: 100%|██████████| 183/183 [00:32<00:00,  5.57it/s, loss=0.584, accuracy=0.725]


Epoch: 3


...

Epoch 1: 100%|██████████| 183/183 [00:33<00:00,  5.45it/s, loss=0.505, accuracy=0.765]


Epoch: 14


Epoch 1: 100%|██████████| 183/183 [00:34<00:00,  5.33it/s, loss=0.459, accuracy=0.786]


Epoch: 15


Epoch 1: 100%|██████████| 183/183 [00:35<00:00,  5.12it/s, loss=0.424, accuracy=0.806]


To finish, let's evaluate the trained model on the test set.

In [ ]:
def evaluate(model: nn.Module, testset: Dataset):
    test_loader = DataLoader(testset, batch_size=32, shuffle=False)

    model.eval()
    y_true, y_pred = [], []
    for batch in test_loader:
        x = batch["tokens"].to(DEVICE)
        y_true += batch["label"].tolist()
        logits = model(x)
        y_pred += logits.argmax(dim=1).tolist()

    return y_true, y_pred

In [ ]:
testset = VIdDataset(dataset["test"], tokenize)
y_true_test, y_pred_test = evaluate(model, testset)

In [ ]:
print(f"First 10 true labels:{y_true_test[:10]}")
print(f"First 10 pred labels:{y_pred_test[:10]}")

First 10 true labels:[1, 0, 0, 0, 1, 1, 1, 0, 1, 0]
First 10 pred labels:[0, 0, 0, 0, 1, 1, 1, 0, 1, 0]


In [ ]:
from sklearn.metrics import classification_report

target_names = [label_map[i] for i in range(n_classes)]
report = classification_report(
    y_true_test,
    y_pred_test,
    target_names=target_names
)
print(report)

              precision    recall  f1-score   support

       PT-PT       0.76      0.88      0.82      1335
       PT-BR       0.84      0.70      0.77      1235

    accuracy                           0.79      2570
   macro avg       0.80      0.79      0.79      2570
weighted avg       0.80      0.79      0.79      2570



In [ ]:
%%capture
!pip install -U transformers
!pip install numpy==1.26.0

In [ ]:
from transformers import BertForSequenceClassification


class Model_2(nn.Module):
  def __init__(self, n_classes: int,
               learning_rate: float,
               batchsize: int,
               dropout_rate: float):

    super(Model_2, self).__init__()
    self.bert = BertForSequenceClassification.from_pretrained("bert-base-multilingual-cased", num_labels=n_classes)

  def forward(self, input_ids):

    outputs = self.bert(input_ids)
    logits = outputs.logits  # Extract logits from BERT output
    return logits



In [ ]:
from torch import optim
from tqdm import tqdm


def train(
    model2: BertForSequenceClassification,
    train_loader: DataLoader,
    n_epochs: int,
    lr: float,
) -> tuple[float, float]:

  optimizer = optim.AdamW(model2.parameters(), lr=lr)
  criteria = nn.CrossEntropyLoss()

  for epoch in range(n_epochs):
    model2.train()

    n_steps = len(train_loader)
    progress_bar = tqdm(
        total=n_steps, desc=f"Epoch {epoch+1}", position=0, leave=True
    )
    total_loss = 0
    total_correct = 0

    for idx, batch in enumerate(train_loader):
      optimizer.zero_grad()
      # Access input_ids and attention_mask from the batch
      input_ids = batch["tokens"].to(DEVICE)
      labels = batch["label"].to(DEVICE)

      # Forward pass through BERT for classification
      outputs = model2(input_ids)
      logits = outputs.logits
      loss = outputs.loss  # Access loss from model output (BertForSequenceClassification)

      loss.backward()
      optimizer.step()

      # Logging and early stopping check
      total_loss += loss.item()
      y_pred = logits.argmax(dim=1)
      total_correct += (y_pred == labels).sum().item()

      progress_bar.set_postfix({
          "loss": total_loss / (idx + 1),
          "accuracy": total_correct / (idx + 1) / input_ids.size(0)
      })
      progress_bar.update()

    avg_loss = total_loss / n_steps
    avg_accuracy = total_correct / (n_steps * input_ids.size(0))

    return avg_loss, avg_accuracy

In [ ]:
from transformers import BertForSequenceClassification

def objective_function(params):

  model2 = Model_2(n_classes=n_classes,
               learning_rate=params['learning_rate'],
               batchsize=params['batchsize'],
               dropout_rate= params['dropout_rate'])

  try:

    avg_loss, _ = train(model2, train_loader, n_epochs=10, lr=params['learning_rate'])


  except Exception as e:
    print(f"Error during training: {e}")
    # Return a large negative value to indicate poor performance
    return -100

  if math.isnan(avg_loss):
    avg_loss = -100
  print(f"avg_loss before return: {avg_loss}")
  return avg_loss

In [ ]:
from hyperopt import hp

search_space = {
  'learning_rate': hp.loguniform('learning_rate', -6, -3),  # Learning rate search space (logarithmic scale)
  'batchsize': hp.quniform('batch_size', 8, 64, 8),  # Batch size search space (uniform with step size 8)
  'dropout_rate': hp.uniform('dropout_rate', 0.1, 0.5),  # Dropout rate search space (uniform)
}


# Optimize the hyperparameters using TPE algorithm (Tree-structured Parzen Estimator)
best_params = fmin(fn=objective_function,
                   space=search_space,
                   algo=tpe.suggest,
                   max_evals=2)



  0%|          | 0/2 [00:00<?, ?trial/s, best loss=?]

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-multilingual-cased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.

Epoch 1:   0%|          | 0/183 [00:56<?, ?it/s]


Error during training: Expected all tensors to be on the same device, but found at least two devices, cpu and cuda:0! (when checking argument for argument index in method wrapper_CUDA__index_select)

  0%|          | 0/2 [00:00<?, ?trial/s, best loss=?]

Epoch 1:   0%|          | 0/183 [00:57<?, ?it/s]


 50%|█████     | 1/2 [00:00<00:00,  1.23trial/s, best loss: -100.0]

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-multilingual-cased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.

Epoch 1:   0%|          | 0/183 [00:57<?, ?it/s]


Error during training: Expected all tensors to be on the same device, but found at least two devices, cpu and cuda:0! (when checking argument for argument index in method wrapper_CUDA__index_select)

 50%|█████     | 1/2 [00:01<00:00,  1.23trial/s, best loss: -100.0]

Epoch 1:   0%|          | 0/183 [00:57<?, ?it/s]


100%|██████████| 2/2 [00:01<00:00,  1.23trial/s, best loss: -100.0]


In [ ]:
best_params

{'batch_size': 16.0,
 'dropout_rate': 0.38466042914271215,
 'learning_rate': 0.004608796763832358}

In [ ]:
best_batchsize = best_params['batch_size']
best_dropout_rate = best_params['dropout_rate']
best_learning_rate = best_params['learning_rate']

model2 = Model_2(n_classes=n_classes,
                 learning_rate=best_learning_rate,
                 batchsize=best_batchsize,
                 dropout_rate=best_dropout_rate)


Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-multilingual-cased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.

Epoch 1:   0%|          | 0/183 [01:03<?, ?it/s]

In [ ]:
 n_epochs= 2
 for epoch in range(n_epochs):
    print(f"Epoch: {epoch+1}")  # Track current epoch
    train(model2, train_loader, n_epochs=n_epochs, lr=best_lr)

Epoch: 1


Epoch 1:   0%|          | 0/183 [00:00<?, ?it/s]

RuntimeError: Expected all tensors to be on the same device, but found at least two devices, cpu and cuda:0! (when checking argument for argument index in method wrapper_CUDA__index_select)



By training a relatively simple model for just one epoch yielded an F1 score of 71%. How might we further enhance this effectiveness? Below are listed some strategies to consider for improving the model:

- **Train on more data** Checkout the DSL-TL on [GitHub](https://github.com/LanguageTechnologyLab/DSL-TL/tree/main/DSL-TL-Corpus/PT-DSL-TL)  or in [huggingface](https://huggingface.co/datasets/LCA-PORVID/dsl_tl) and the [FRMT](https://huggingface.co/datasets/LCA-PORVID/frmt) dataset.

- **Increase the model capacity** Increase the number of layers or the hidden size.
- **Hyperparameter Optimization** For instance, what is learning rate that produces the best model.
- **Incorporate Pre-trained Components**
  - For **word embeddings** you might find [fasttext](https://fasttext.cc/docs/en/crawl-vectors.html) or [GloVE](https://nlp.stanford.edu/projects/glove/) as good starting points.
  - For **language models**, [albertina](https://huggingface.co/PORTULAN/albertina-100m-portuguese-ptpt-encoder) or [bertimbau](https://huggingface.co/neuralmind/bert-base-portuguese-cased) should yield interesting results.

https://medium.com/geekculture/10-hyperparameters-to-keep-an-eye-on-for-your-lstm-model-and-other-tips-f0ff5b63fcd4
https://towardsdatascience.com/language-modeling-with-lstms-in-pytorch-381a26badcbf

https://arxiv.org/pdf/1412.6980

